# Economic Indicators

In [19]:
import pandas as pd
import pandas_profiling
import numpy as np
from sqlalchemy import create_engine

In [20]:
cpi = pd.read_csv('Data/CPI.csv')
college = pd.read_csv('Data/college_prices.csv')
salary = pd.read_csv('Data/median_income.csv')
mortgage = pd.read_csv('Data/30_yr_mortgages.csv')
gas = pd.read_csv('Data/Gasoline_prices.csv')
house = pd.read_csv('Data/median_house_price.csv')
population = pd.read_csv('Data/population.csv')

## Renaming columns

In [21]:
cpi = cpi.rename(columns={'DATE': 'Date', 'MEDCPIM158SFRBCLE': 'CPI'})
college = college.rename(columns={'Year': 'Date', 'Public 4-Year': 'Public', 'Private 4-Year': 'Private'})
salary = salary.rename(columns={'DATE': 'Date', 'MEHOINUSA672N': 'Salary'})
mortgage = mortgage.rename(columns={'DATE': 'Date', 'MORTGAGE30US': '30-yr Mortgage'})
gas = gas.rename(columns={'DATE': 'Date', 'APU000074714': 'Gas Prices'})
house = house.rename(columns={'DATE': 'Date', 'MSPUS': 'Median Sale Price'})
population = population.rename(columns={'DATE': 'Date', 'POPTHM': 'Population'})

## Converting to date-time formats

In [22]:
cpi['Date'] = pd.to_datetime(cpi.Date)
salary['Date'] = pd.to_datetime(salary.Date)
#turning each year into months
salary = salary.set_index('Date').resample('MS').bfill().reset_index()
mortgage['Date'] = pd.to_datetime(mortgage.Date)
mortgage = mortgage.set_index('Date').resample('MS').bfill().reset_index()
gas['Date'] = pd.to_datetime(gas.Date)
house['Date'] = pd.to_datetime(house.Date)
population['Date'] = pd.to_datetime(population.Date)

In [23]:
college['Date'] = college["Date"].str.split('-').str[0]
college['Date'] = pd.to_datetime(college.Date, format='%Y')
college = college.set_index('Date').resample('MS').ffill().reset_index()

In [24]:
college['Public'] = college["Public"].str.replace("$", "")
college['Private'] = college["Private"].str.replace("$", "")
college['Public'] = college["Public"].replace("Unavailable", np.nan, regex=True)
college['Private'] = college["Private"].replace("Unavailable", np.nan, regex=True)
college['Public'] = college["Public"].str.replace(",", "")
college['Private'] = college["Private"].str.replace(",", "")
college['Public'] = college['Public'].astype(float)
college['Private'] = college['Private'].astype(float)
college['Public'] = college['Public'].interpolate(method = 'linear')
college['Private'] = college['Private'].interpolate(method = 'linear')

/var/folders/qz/jcfsjj450mj445q0fztf5q3r0000gn/T/ipykernel_11524/3728055962.py:1: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  college['Public'] = college["Public"].str.replace("$", "")
/var/folders/qz/jcfsjj450mj445q0fztf5q3r0000gn/T/ipykernel_11524/3728055962.py:2: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  college['Private'] = college["Private"].str.replace("$", "")


In [300]:
mortgage.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [301]:
cpi.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [303]:
college.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [304]:
salary.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [305]:
gas.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [306]:
house.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [307]:
population.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [34]:
connection_string = "postgres:postgres@localhost:5432/econ_db"
engine = create_engine(f'postgresql://{connection_string}')

In [35]:
cpi.to_sql(name='cpi', con=engine, if_exists='append', index=False)
college.to_sql(name='college', con=engine, if_exists='append', index=False)
salary.to_sql(name='salary', con=engine, if_exists='append', index=False)
mortgage.to_sql(name='mortgage', con=engine, if_exists='append', index=False)
gas.to_sql(name='gas', con=engine, if_exists='append', index=False)
house.to_sql(name='house', con=engine, if_exists='append', index=False)
population.to_sql(name='population', con=engine, if_exists='append', index=False)

In [36]:
pd.read_sql_query('select * from college', con=engine).head()

Date  Public  Private
0 1963-01-01   243.0   1011.0
1 1963-02-01   243.0   1011.0
2 1963-03-01   243.0   1011.0
3 1963-04-01   243.0   1011.0
4 1963-05-01   243.0   1011.0